In [ ]:
"""

Contains the necessary scripts to actually download the FITS files that are in your JWST csv.


"""

In [ ]:
import pandas as pd
import numpy as np
from astropy.coordinates import SkyCoord
from astropy import units as u
from sklearn.cluster import AgglomerativeClustering
import matplotlib.pyplot as plt
import matplotlib.patches as patches
import os
import numpy as np
from astropy.io import fits
from astropy.wcs import WCS
from tqdm import tqdm

df = pd.read_csv("jwst_FINAL.csv")

df = df.rename(columns={'sci_data_set_name': 'obs_id'})

# Effective integration time should be more than 30 seconds
df = df[df['effinttm'] > 30]

df = df[df['exp_type'] == "NRC_IMAGE"]

"""
The data downloading process looks like the following:

1. Use MastMissions to query the list of observations and their metadata, like ra/dec

2. Filtering process to make sure there are no overlapping observations.

3. Use Observations to pull the names of the data files associated with each observation.

4. Pull the data by wget all those file links.

5. Preprocess.

Note that the data file names use the first 6 chars of obs_id from this observations array
that we have created. That's why we create the shortened identifier, to match
observations to product file names. This will be used later.
"""

df['obs_id_short'] = df['obs_id'].str[:6]

RA_NAME = 'targ_ra'
DEC_NAME = 'targ_dec'

assert df[RA_NAME].isna().sum() < 10
assert df[DEC_NAME].isna().sum() < 10

df = df.dropna(subset=[RA_NAME, DEC_NAME])

df = df.groupby([RA_NAME, DEC_NAME]).apply(lambda x: x.drop_duplicates(subset='detector', keep='first'))

multi_index_df = df.index.to_frame().groupby(level=0).first().reset_index(drop=True)
multi_index_df = multi_index_df.drop(columns=[2])

df = df.reset_index(drop=True)

In [173]:
import requests
import csv

# Function to search datasets using the given endpoint
def search_datasets(dataset_ids):
    # Base URL for the search API
    base_url = 'https://mast.stsci.edu/search/jwst/api/v0.1/list_products'
    
    # List to store search results
    search_results = []
    
    ids_str = ','.join(dataset_ids)

    # Construct the search URL
    search_url = f"{base_url}?dataset_ids={ids_str}"

    # Make the API request
    response = requests.get(search_url)

    # Check if the request was successful
    if response.status_code == 200:
        # Parse the JSON response
        data = response.json()
        search_results.append(data)
    else:
        # Handle errors
        print(f"Error: Unable to fetch data for dataset ID {dataset_id}")
    
    return search_results

# Example usage
dataset_ids_csv = list(df['fileSetName'])

sz_chunk = 10
chunks = [dataset_ids_csv[i:i+sz_chunk] for i in range(0,len(dataset_ids_csv), sz_chunk)]

all_results = []

for chunk in tqdm(chunks):
    all_results.append(search_datasets(chunk))

100%|█████████████████████████████████████████| 117/117 [13:48<00:00,  7.08s/it]


In [179]:
new_all_results = []

for result in tqdm(all_results):
    l = result[0]['products']
    new_all_results.extend(l)

100%|███████████████████████████████████████| 117/117 [00:00<00:00, 3803.87it/s]


In [181]:
new_all_results_df = pd.DataFrame(new_all_results)

In [184]:
detectors = ['NRCA1_FULL', 'NRCA2_FULL', 'NRCA3_FULL', 'NRCA4_FULL', 'NRCB1_FULL', 'NRCB2_FULL', 'NRCB3_FULL', 'NRCB4_FULL']


resultsdf = new_all_results_df[new_all_results_df['category'] == '1b']
resultsdf = resultsdf[resultsdf['filters'].isin(detectors)]

In [189]:
resultsdf

product_key  access  \
28      jw02561001002_06101_00001_jw02561001002_06101_...  PUBLIC   
50      jw02561001002_06101_00001_jw02561001002_06101_...  PUBLIC   
72      jw02561001002_06101_00001_jw02561001002_06101_...  PUBLIC   
93      jw02561001002_06101_00001_jw02561001002_06101_...  PUBLIC   
114     jw02561001002_06101_00001_jw02561001002_06101_...  PUBLIC   
...                                                   ...     ...   
216718  jw02130007001_03101_00002_jw02130007001_03101_...  PUBLIC   
216740  jw02130007001_03101_00002_jw02130007001_03101_...  PUBLIC   
216786  jw02130007001_03101_00002_jw02130007001_03101_...  PUBLIC   
216808  jw02130007001_03101_00002_jw02130007001_03101_...  PUBLIC   
216830  jw02130007001_03101_00002_jw02130007001_03101_...  PUBLIC   

                          dataset instrument_name     filters  \
28      jw02561001002_06101_00001          NIRCAM  NRCA3_FULL   
50      jw02561001002_06101_00001          NIRCAM  NRCB3_FULL   
72      jw02561001002_06101_00001          NIRCAM  NRCA2_FULL   
93      jw02561001002_06101_00001          NIRCAM  NRCB2_FULL   
114     jw02561001002_06101_00001          NIRCAM  NRCA4_FULL   
...                           ...             ...         ...   
216718  jw02130007001_03101_00002          NIRCAM  NRCB1_FULL   
216740  jw02130007001_03101_00002          NIRCAM  NRCA4_FULL   
216786  jw02130007001_03101_00002          NIRCAM  NRCA1_FULL   
216808  jw02130007001_03101_00002          NIRCAM  NRCA3_FULL   
216830  jw02130007001_03101_00002          NIRCAM  NRCA2_FULL   

                                          filename  \
28      jw02561001002_06101_00001_nrca3_uncal.fits   
50      jw02561001002_06101_00001_nrcb3_uncal.fits   
72      jw02561001002_06101_00001_nrca2_uncal.fits   
93      jw02561001002_06101_00001_nrcb2_uncal.fits   
114     jw02561001002_06101_00001_nrca4_uncal.fits   
...                                            ...   
216718  jw02130007001_03101_00002_nrcb1_uncal.fits   
216740  jw02130007001_03101_00002_nrca4_uncal.fits   
216786  jw02130007001_03101_00002_nrca1_uncal.fits   
216808  jw02130007001_03101_00002_nrca3_uncal.fits   
216830  jw02130007001_03101_00002_nrca2_uncal.fits   

                                                      uri  \
28      jw02561001002_06101_00001/jw02561001002_06101_...   
50      jw02561001002_06101_00001/jw02561001002_06101_...   
72      jw02561001002_06101_00001/jw02561001002_06101_...   
93      jw02561001002_06101_00001/jw02561001002_06101_...   
114     jw02561001002_06101_00001/jw02561001002_06101_...   
...                                                   ...   
216718  jw02130007001_03101_00002/jw02130007001_03101_...   
216740  jw02130007001_03101_00002/jw02130007001_03101_...   
216786  jw02130007001_03101_00002/jw02130007001_03101_...   
216808  jw02130007001_03101_00002/jw02130007001_03101_...   
216830  jw02130007001_03101_00002/jw02130007001_03101_...   

                          authz_primary_identifier  \
28      jw02561001002_06101_00001_nrca3_uncal.fits   
50      jw02561001002_06101_00001_nrcb3_uncal.fits   
72      jw02561001002_06101_00001_nrca2_uncal.fits   
93      jw02561001002_06101_00001_nrcb2_uncal.fits   
114     jw02561001002_06101_00001_nrca4_uncal.fits   
...                                            ...   
216718  jw02130007001_03101_00002_nrcb1_uncal.fits   
216740  jw02130007001_03101_00002_nrca4_uncal.fits   
216786  jw02130007001_03101_00002_nrca1_uncal.fits   
216808  jw02130007001_03101_00002_nrca3_uncal.fits   
216830  jw02130007001_03101_00002_nrca2_uncal.fits   

                        authz_secondary_identifier file_suffix category  \
28      jw02561001002_06101_00001_nrca3_uncal.fits      _uncal       1b   
50      jw02561001002_06101_00001_nrcb3_uncal.fits      _uncal       1b   
72      jw02561001002_06101_00001_nrca2_uncal.fits      _uncal       1b   
93      jw02561001002_06101_00001_nrcb2_uncal.fits      _uncal       1b   
114     jw02561001002_06101_00

In [188]:
resultsdf.to_csv("all_jwst_uris.csv")

In [145]:
# Array of latitudes and longitudes
# MAKE SURE TO PUT RA=LON, DEC=LAT
latitudes = np.array(multi_index_df.groupby(level=0).first()[DEC_NAME])  # Example latitudes
longitudes = np.array(multi_index_df.groupby(level=0).first()[RA_NAME])  # Example longitudes

n_points = len(latitudes)

# Repeat each point n_points times for lat1, lon1
lat1 = np.repeat(latitudes, n_points)
lon1 = np.repeat(longitudes, n_points)

# Tile the whole array n_points times for lat2, lon2
lat2 = np.tile(latitudes, n_points)
lon2 = np.tile(longitudes, n_points)

# Calculates angular separation between two spherical coords
# This can be lat/lon or ra/dec
# Taken from astropy
def angular_separation_deg(lon1, lat1, lon2, lat2):
    lon1 = np.deg2rad(lon1)
    lon2 = np.deg2rad(lon2)
    lat1 = np.deg2rad(lat1)
    lat2 = np.deg2rad(lat2)
    
    sdlon = np.sin(lon2 - lon1)
    cdlon = np.cos(lon2 - lon1)
    slat1 = np.sin(lat1)
    slat2 = np.sin(lat2)
    clat1 = np.cos(lat1)
    clat2 = np.cos(lat2)

    num1 = clat2 * sdlon
    num2 = clat1 * slat2 - slat1 * clat2 * cdlon
    denominator = slat1 * slat2 + clat1 * clat2 * cdlon

    return np.rad2deg(np.arctan2(np.hypot(num1, num2), denominator))

# Compute the pairwise angular separations
angular_separations = angular_separation_deg(lon1, lat1, lon2, lat2)

# Reshape the result into a matrix form
angular_separations_matrix = angular_separations.reshape(n_points, n_points)

def check_symmetric(a, rtol=1e-05, atol=1e-07):
    return np.allclose(a, a.T, rtol=rtol, atol=atol)

print("Symmetric?")
print(check_symmetric(angular_separations_matrix))
print(angular_separations_matrix.shape)

Symmetric?
True
(475, 475)


In [84]:
#HUBBLE_FOV = 0.057
JWST_FOV = 0.0366667

THRESH = JWST_FOV

"""
Initial clustering and filtering using single RA DEC value.

"""

clustering = AgglomerativeClustering(n_clusters=None, metric='precomputed', linkage='single', distance_threshold=THRESH)
labels = clustering.fit_predict(angular_separations_matrix)

multi_index_df['label'] = labels

print(pd.Series(labels).value_counts())

def max_subset_with_min_distance(points, min_distance):
    subset = []
    for i, row in points.iterrows():
        if all(angular_separation_deg(row[RA_NAME], row[DEC_NAME], existing_point[RA_NAME], existing_point[DEC_NAME]) >= min_distance for existing_point in subset):
            subset.append(row)
    return subset

all_subsets = []

for label in tqdm(np.unique(labels)):
    cds = multi_index_df[multi_index_df['label'] == label]
    subset = max_subset_with_min_distance(cds, THRESH)
    all_subsets.extend(subset)

print("Max subset with minimum distance:", len(all_subsets))

locations = pd.DataFrame(all_subsets)

df = pd.merge(df, locations, on=[RA_NAME, DEC_NAME], how='right')

print(len(df))

24     40
12     40
76     36
34     30
7      24
       ..
221     1
166     1
139     1
176     1
20      1
Length: 311, dtype: int64


100%|███████████████████████████████████████| 311/311 [00:00<00:00, 3456.86it/s]

Max subset with minimum distance: 321
1110


In [107]:
detectors = ['nrca1', 'nrca2', 'nrca3', 'nrca4', 'nrcb1', 'nrcb2', 'nrcb3', 'nrcb4']
obsids_search = []

for fileset in df['fileSetName']:
    for detector in detectors:
        obsids_search.append(fileset + "_" + detector)

In [108]:
from astroquery.mast import Observations

# Query for data with the specified obs_id
result = Observations.query_criteria(obs_id=obsids_search)

In [120]:
from astropy.table import unique, vstack, Table

"""
Call API that gives the file URLs for each observations.

"""

matched_obs = result

# Split the observations into "chunks" of size five
sz_chunk = 5
chunks = [matched_obs[i:i+sz_chunk] for i in range(0,len(matched_obs), sz_chunk)]

# Get the list of products for each chunk
t = []
for chunk in tqdm(chunks):
    t.append(Observations.get_product_list(chunk))

files = unique(vstack(t), keys='productFilename')
files = files.to_pandas()

# Ensure we only keep raw data files
files = files[files['productSubGroupDescription'] == 'UNCAL']

# Create a shortened identified
files['obs_id_short'] = files['obs_id'].str[:6]

print(f"There are {len(files)} unique files, which are {sum(files['size'])/10**9:.1f} GB in size.")

manifest = Observations.download_products(files['obsID'], curl_flag=True)

100%|█████████████████████████████████████████| 108/108 [01:07<00:00,  1.60it/s]


There are 0 unique files, which are 0.0 GB in size.


ValueError: no values provided to stack.

In [ ]:
files[['obsID']].to_csv('list_of_hubble_filenames.csv')

In [ ]:
manifest = Observations.download_products(files['obsID'], curl_flag=True)
# Creates .sh scripts that have to then be run to actually download data

In [ ]:
import numpy as np
from astropy.io import fits
from astropy.table import Table
import glob

"""
This code allows us to combine multiple exposures of the same observation into one FITS file.

This code was NOT used; we only used a single exposure for our dataset.
"""

def create_combined_hubble_file(short_obs_id):
    
    file_list = list(files[files['obs_id_short'] == short_obs_id]['productFilename'])
    
    ccd1_data = []
    ccd2_data = []
    ccd1_times = []
    ccd2_times = []
    ccd1_headers = []
    ccd2_headers = []

    for file in file_list:
        with fits.open(file) as hdul:
            # Extract TIME-OBS from the primary header
            time_obs = hdul[0].header['TIME-OBS']

            # Extract data and headers from HDUs
            for hdu in [hdul[1], hdul[4]]:
                if hdu.header['CCDCHIP'] == 1:
                    ccd1_data.append(hdu.data)
                    ccd1_times.append(time_obs)
                    ccd1_headers.append(hdul[0].header.copy())
                elif hdu.header['CCDCHIP'] == 2:
                    ccd2_data.append(hdu.data)
                    ccd2_times.append(time_obs)
                    ccd2_headers.append(hdul[0].header.copy())

    # Sort the data based on TIME-OBS
    ccd1_times, ccd1_data, ccd1_headers = zip(*sorted(zip(ccd1_times, ccd1_data, ccd1_headers)))
    ccd2_times, ccd2_data, ccd2_headers = zip(*sorted(zip(ccd2_times, ccd2_data, ccd2_headers)))

    # Concatenate the data for each CCDCHIP
    ccd1_concat = np.stack(ccd1_data)
    ccd2_concat = np.stack(ccd2_data)

    # Function to create a new FITS file for a given CCDCHIP
    def create_fits_file(output_file, ccd_data, ccd_headers, ccd_chip):

        primary_hdu = fits.PrimaryHDU()
        primary_hdu.header['EXTEND'] = True
        primary_hdu.header['CCDCHIP'] = ccd_chip

        metadata_hdus = [fits.ImageHDU(header=header) for header in ccd_headers]

        # Create ImageHDU with concatenated data
        image_hdu = fits.ImageHDU(data=ccd_data, header=fits.Header({'CCDCHIP': ccd_chip}))

        # Create HDUList and write to a new FITS file
        hdulist = fits.HDUList([primary_hdu] + [image_hdu] + metadata_hdus)
        hdulist.writeto(output_file, overwrite=True)

    # Create FITS files for CCDCHIP 1 and 2
    create_fits_file(f'{short_obs_id}_ccd1.fits', ccd1_concat, ccd1_headers, 1)
    create_fits_file(f'{short_obs_id}_ccd2.fits', ccd2_concat, ccd2_headers, 2)

    print("New FITS files created successfully.")

In [ ]:
def visualize_label(df, LABEL=None):
    
    cds = df
    
    if LABEL is not None:
        cds = cds[labels == LABEL]

    ras, decs = [], []
    cmap = []
    
    print(len(cds))

    for i, cd in cds.iterrows():
        ras.append(cd[RA_NAME])
        decs.append(cd[DEC_NAME])

    if LABEL is None:
        # No gridlines, will be overwhelming

        # Compute the 2D histogram
        # Number of bins for x and y; adjust these based on your dataset
        bins = (30, 30)

        # Compute the histogram
        hist, xedges, yedges = np.histogram2d(ras, decs, bins=bins)
        
        N_cutoff = 50
        hist = np.clip(hist, 0, N_cutoff)

        # Generate a 2D histogram plot
        plt.figure(figsize=(8, 6))
        plt.imshow(hist, interpolation='nearest', origin='lower',
                   extent=[xedges[0], xedges[-1], yedges[0], yedges[-1]],
                   cmap='viridis')  # Choose a colormap (e.g., 'viridis', 'plasma', 'inferno')

        # Add labels and title if necessary
        plt.colorbar(label='Number of points in bin')
        plt.xlabel('RA')
        plt.ylabel('DEC')
        plt.title(f'2D Histogram of Point Density, clipped to {N_cutoff} points')

        # Show the plot
        plt.show()

        return
    else:
        fig = plt.figure()
        ax = fig.gca()
        ax.set_xticks(np.arange(np.min(ras), np.max(ras), THRESH))
        ax.set_yticks(np.arange(np.min(decs), np.max(decs), THRESH))
        plt.scatter(ras, decs, alpha=0.1)
        plt.grid()
        plt.show()

visualize_label(df, 7)

In [ ]:
from sklearn.model_selection import train_test_split

data = list(range(len(labels)))

# Perform the train-test split with an 80-20 ratio
train_indices, test_indices = train_test_split(data, test_size=0.2, random_state=42)

In [ ]:
sdss_test = all_sdss_data[all_sdss_data['cluster_label'].isin(test_indices)]
sdss_train = all_sdss_data[all_sdss_data['cluster_label'].isin(train_indices)]

In [ ]:
len(sdss_test)

In [ ]:
len(sdss_train)

In [ ]:
sdss_test

In [ ]:
test_data = pd.DataFrame(test_data)
train_data = pd.DataFrame(train_data)

In [ ]:
"""
Code to verify test/train pollution.
Prints images which are nearby and might overlap.
"""


import json
from math import radians, sin, cos, sqrt, atan2, degrees
import numpy as np
import matplotlib.pyplot as plt


# Function to load data from file
def load_data(file_path):
    data = []
    with open(file_path, 'r') as f:
        for line in f:
            data.append(json.loads(line))
    return data

# Load data
train_file_path = '/Users/rithwik/Desktop/full_train.jsonl.txt'
test_file_path = '/Users/rithwik/Desktop/full_test.jsonl.txt'
#train_data = sdss_train
#test_data = sdss_test

# Define the threshold
threshold = 0.09*3

# Find test dataset rows with a minimum great circle distance less than the threshold
close_pairs = []

for i, test_point in test_data.iterrows():
    ra_test, dec_test = test_point['ra'], test_point['dec']
    distances = [(train_point, angular_separation_deg(ra_test, dec_test, train_point['ra'], train_point['dec'])) for i, train_point in train_data.iterrows()]
    closest_train_point, min_distance = min(distances, key=lambda x: x[1])
    if min_distance < threshold:
        close_pairs.append((test_point, closest_train_point, min_distance))

close_pairs_summary = [
    {
        "test_image_id": test_point['image_id'],
        "test_ra": test_point['ra'],
        "test_dec": test_point['dec'],
        "train_image_id": closest_train_point['image_id'],
        "train_ra": closest_train_point['ra'],
        "train_dec": closest_train_point['dec'],
        "min_distance_deg": min_distance
    }
    for test_point, closest_train_point, min_distance in close_pairs
]

# Print the results
result = "Success"
for pair in close_pairs_summary:
    print(pair)
    result = "FAIL"
    
print(f"Done. result is {result}")

In [ ]:
sdss_test.to_json('full_test1.jsonl', orient='records', lines=True)
sdss_train.to_json('full_train1.jsonl', orient='records', lines=True)